In [22]:
#Data Manipulation
import pandas as pd
pd.set_option('display.max_columns', None)
import numpy as np
import math

#Data visualization
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
colors = ['#c1121f','#669bbc', '#f4d35e', '#e9724c', '#ffc857']
plt.style.use('seaborn-white')
plt.rc('figure', figsize=(12,8))
plt.rc('font', size=18)
plt.rc('axes', labelsize=14, titlesize=14)
plt.rc('legend', fontsize=14)
plt.rc('xtick', labelsize=10)
plt.rc('ytick', labelsize=10)

#Preprocessing
from sklearn.model_selection import train_test_split
import sklearn.utils
from sklearn.utils.validation import check_array, check_is_fitted
from sklearn.feature_selection import SelectKBest, chi2
from sklearn.model_selection import train_test_split
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import FunctionTransformer
from sklearn.compose import ColumnTransformer

#Models
import tensorflow as tf

#Metrics and Tuning
from sklearn.metrics import balanced_accuracy_score
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.metrics import mean_squared_error
from sklearn.metrics import r2_score
from sklearn.metrics import make_scorer
from yellowbrick.regressor import PredictionError, ResidualsPlot

#General
import os
from google.colab import files
import warnings
warnings.filterwarnings(action='ignore')

In [2]:
sustainability = pd.read_csv("/content/sustainability.csv")
rural = pd.read_csv("/content/rural.csv")
energy = pd.read_csv("/content/energy.csv")
argicultural = pd.read_csv("/content/argicultural_inputs.csv")
climate = pd.read_csv("/content/climate.csv")
emissions = pd.read_csv("/content/emissions.csv")
freshwater = pd.read_csv("/content/freshwater.csv")
greenhouse_gas_emissions = pd.read_csv("/content/greenhouse_gas_emissions.csv")
health_system = pd.read_csv("/content/health_system.csv")
Health_Risk_factors = pd.read_csv("/content/Health_Risk_factors only tb.csv")
# merge the DataFrames on Country
merged1_df = sustainability.merge(rural, on="Country")
# merge the DataFrames on Country
merged2_df = merged1_df.merge(energy, on="Country")
# merge the DataFrames on Country
merged3_df = merged2_df.merge(argicultural, on="Country")
# merge the DataFrames on Country
merged4_df = merged3_df.merge(climate, on="Country")
# merge the DataFrames on Country
merged5_df = merged4_df.merge(emissions, on="Country")
# merge the DataFrames on Country
merged6_df = merged5_df.merge(freshwater, on="Country")
# merge the DataFrames on Country
merged7_df = merged6_df.merge(greenhouse_gas_emissions, on="Country")
# merge the DataFrames on Country
merged8_df = merged7_df.merge(health_system, on="Country")
#merge the DataFrames on Country
df = merged8_df.merge(Health_Risk_factors, on="Country")
df.head()

Country  \
0     Afghanistan   
1         Albania   
2         Algeria   
3  American Samoa   
4         Andorra   

   People using  safely managed drinking water services  % of population 2017  \
0                                                NaN                            
1                                               70.0                            
2                                                NaN                            
3                                               12.6                            
4                                               90.6                            

   People using  safely managed sanitation services  % of population 2017  \
0                                                NaN                        
1                                               39.9                        
2                                               17.7                        
3                                                NaN                        
4                                              100.0                        

   Access to electricity  % of population 2017  \
0                                         97.7   
1                                        100.0   
2                                        100.0   
3                                          NaN   
4                                        100.0   

   Renewable energy consumption  % of total final energy consumption 2015_x  \
0                                               18.4                          
1                                               38.6                          
2                                                0.1                          
3                                                0.9                          
4                                               19.7                          

   Expenditures for R&D  % of GDP 2015  \
0                                  NaN   
1                                  NaN   
2                                  0.5   
3                                  NaN   
4                                  NaN   

   Urban population living in slums  % of urban population 2014  \
0                                               62.7              
1                                                NaN              
2                                                NaN              
3                                                NaN              
4                                                NaN              

   Ambient PM2.5 air pollution mean annual exposure micrograms per cubic meter 2016  \
0                                               56.3                                  
1                                               18.2                                  
2                                               39.9                                  
3                                               12.4                                  
4                                               10.3                                  

   Adjusted net savings  % of GNI 2017  \
0                                  2.7   
1                                  8.2   
2                                 21.2   
3                                  NaN   
4                                  NaN   

   Carbon dioxide emissions per capita metric tons 2014_x  \
0                                                0.3        
1                                                2.0        
2                                                3.7        
3                                                NaN        
4                                                5.8        

   Nationally protected terrestrial and marine areas  % of total territorial area 2018  \
0                                                0.1                                     
1                                               13.5                                     
2                                                7.1                                    

In [3]:
print('------ Dataset ------')
print(f'Number of rows: {df.shape[0]}')
print(f'Number of columns: {df.shape[1]}')

------ Dataset ------
Number of rows: 214
Number of columns: 100


In [4]:
df = df.replace('', np.nan)  # Replace empty values with NaN

In [5]:
df.columns

Index(['Country',
       'People using  safely managed drinking water services  % of population 2017',
       'People using  safely managed sanitation services  % of population 2017',
       'Access to electricity  % of population 2017',
       'Renewable energy consumption  % of total final energy consumption 2015_x',
       'Expenditures for R&D  % of GDP 2015',
       'Urban population living in slums  % of urban population 2014',
       'Ambient PM2.5 air pollution mean annual exposure micrograms per cubic meter 2016',
       'Adjusted net savings  % of GNI 2017',
       'Carbon dioxide emissions per capita metric tons 2014_x',
       'Nationally protected terrestrial and marine areas  % of total territorial area 2018',
       'Intentional homicides Combined source estimates per 100,000 people 2015',
       'Internet use Individuals using the Internet % of population 2017',
       'Rural population  % of total 2000',
       'Rural population  % of total 2018',
       'Rural populat

In [6]:
#Fix columns names formatting errors
columns_name_fixed = []

for column in df.columns:
    if column == ' tuberculosis  per 100,000 ':
        column = 'tuberculosis  per 100,000'
    else:
        column = column.strip(' ').replace("  ", " ")
        column = column[:1].upper() + column[1:]

    columns_name_fixed.append(column)

df.columns = columns_name_fixed

In [8]:
plt.figure(figsize=(100,100))

heatmap_colors = [colors[1], '#d6d5c9', colors[0]]

corr = df.corr()
mask = np.triu(np.ones_like(corr, dtype=bool))

sns.heatmap(df.corr(),
            mask=mask,
            center=0,
            annot=True,
            fmt='.2f',
            cmap=heatmap_colors,
            square=True,
            linewidths=.2,
            cbar_kws={"shrink": .6})

plt.title('Features Correlation Matrix Heatmap', fontsize=25);
plt.savefig('Features Correlation Matrix Heatmap.png')
files.download('Features Correlation Matrix Heatmap.png')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [11]:
#  set diagonal elements to zero
corr.values[[i for i in range(corr.shape[0])], [i for i in range(corr.shape[0])]] = 0

# Step 1: Filter the correlation matrix to keep only the desired column
tb_corr = corr["Incidence of tuberculosis per 100,000 people 2018"]



sorted_corr = corr["Incidence of tuberculosis per 100,000 people 2018"].sort_values(ascending=False)
print(sorted_corr[0:20])

Agricultural employment % of total employment 2014-16                                                                              0.579684
Agricultural employment % of total employment 2000-02                                                                              0.568611
Renewable energy consumption % of total final energy consumption 2000                                                              0.487064
Renewable energy consumption % of total final energy consumption 2015_x                                                            0.437801
Renewable energy consumption % of total final energy consumption 2015_y                                                            0.437801
External health expenditure (% of current health expenditure)  2016                                                                0.430878
Rural population % of total 2000                                                                                                   0.414036
Annual freshwater wi

In [14]:
print(sorted_corr[80:100])

Carbon dioxide emissions per capita metric tons 1990                                   -0.357972
Agricultural machinery tractors per 100 sq. km of arable land 2000                     -0.377540
Health expenditure per capita $ 2016                                                   -0.379820
Health workers Nurses and midwives per 1,000 people 2009-18                            -0.410219
People using at least basic drinking water services Urban % of urban population 2018   -0.432430
People using safely managed sanitation services % of population 2017                   -0.435697
Specialist surgical workforce per 100,000 population 2008-18                           -0.461213
Health workers Physicians per 1,000 people 2009-18                                     -0.469281
Completeness of birth registration % 2009-18                                           -0.490849
Access to electricity % of urban population 2016                                       -0.528112
Access to electricity % of pop

In [15]:
df.set_index("Country", inplace = True)

In [18]:
print("Before filling NaN values:")
print(df.isnull().sum())

for column in df.columns:
    # Calculate the column mean, excluding NaN values
    column_mean = df[column].mean(skipna=True)
    # Fill NaN values with the calculated mean
    df[column] = df[column].fillna(column_mean)
    # Check for NaN values after filling
print("\nAfter filling NaN values:")
print(df.isnull().sum())

Before filling NaN values:
People using safely managed drinking water services % of population 2017    106
People using safely managed sanitation services % of population 2017        120
Access to electricity % of population 2017                                    2
Renewable energy consumption % of total final energy consumption 2015_x       4
Expenditures for R&D % of GDP 2015                                           89
                                                                           ... 
Health workers Nurses and midwives per 1,000 people 2009-18                  25
Specialist surgical workforce per 100,000 population 2008-18                 39
Completeness of birth registration % 2009-18                                 51
Completeness of death registration % 2008-16                                107
Incidence of tuberculosis per 100,000 people 2018                             7
Length: 99, dtype: int64

After filling NaN values:
People using safely managed drinking wate

In [20]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 214 entries, Afghanistan to Zimbabwe
Data columns (total 99 columns):
 #   Column                                                                                                                           Non-Null Count  Dtype  
---  ------                                                                                                                           --------------  -----  
 0   People using safely managed drinking water services % of population 2017                                                         214 non-null    float64
 1   People using safely managed sanitation services % of population 2017                                                             214 non-null    float64
 2   Access to electricity % of population 2017                                                                                       214 non-null    float64
 3   Renewable energy consumption % of total final energy consumption 2015_x                   

In [27]:
df['output'] = [0 if i < 100 else 1 for i in df['Incidence of tuberculosis per 100,000 people 2018']]

In [28]:
df.columns

Index(['People using safely managed drinking water services % of population 2017',
       'People using safely managed sanitation services % of population 2017',
       'Access to electricity % of population 2017',
       'Renewable energy consumption % of total final energy consumption 2015_x',
       'Expenditures for R&D % of GDP 2015',
       'Urban population living in slums % of urban population 2014',
       'Ambient PM2.5 air pollution mean annual exposure micrograms per cubic meter 2016',
       'Adjusted net savings % of GNI 2017',
       'Carbon dioxide emissions per capita metric tons 2014_x',
       'Nationally protected terrestrial and marine areas % of total territorial area 2018',
       'Intentional homicides Combined source estimates per 100,000 people 2015',
       'Internet use Individuals using the Internet % of population 2017',
       'Rural population % of total 2000', 'Rural population % of total 2018',
       'Rural population growth (annual %)  2018',
       

In [29]:
df.to_csv('data_after_processing_all_100_factors.csv', index=True)

# Download the CSV file to your local machine
files.download('data_after_processing_all_100_factors.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [30]:
#Class to replace outliers
class OutliersRemover(BaseEstimator, TransformerMixin):
    def __init__(self, baseline=1.5):
        self.baseline = baseline

    def fit(self, X, y=None):
        X = check_array(X, force_all_finite=False) #If non-array, transform into an array
        q1 = np.nanquantile(X, 0.25, axis=0) #First quartile
        q3 = np.nanquantile(X, 0.75, axis=0) #Third quartile
        IQR = q3 - q1
        self.lower_bound = q1 - (self.baseline * IQR)
        self.upper_bound = q3 + (self.baseline * IQR)
        self.n_features_in_ = X.shape[1]
        return self

    def transform(self, X, y=None):
        check_is_fitted(self)
        X = check_array(X, force_all_finite=False)
        assert self.n_features_in_ == X.shape[1]
        X_transformed = X.copy()
        X_transformed = np.where(((X_transformed < self.lower_bound) | (X_transformed > self.upper_bound)),
                                 np.nan,
                                 X_transformed)


        return X_transformed #Returns an array

In [31]:
def plot_boxplot(df, columns, title = 'Box plot of features'):

    df = df.copy()

    rows = math.ceil(len(columns)/2)

    fig, ax = plt.subplots(rows, 2, figsize = (100,100))

    for i, column in enumerate(columns):
        ax = plt.subplot(rows, 2, i+1)

        sns.boxplot(x = df[column],
                    data = df,
                    ax = ax,
                    color = colors[0])

        ax.set_xlabel(column)
        ax.set_ylabel('')

    fig.suptitle(title,
                 fontsize=24,
                 x = 0.56);

    fig.text(0.04, 0.5,
             'Density',
             va='center',
             rotation='vertical',
             fontsize=16)

    fig.tight_layout(rect=[0.05, 0.03, 1, 1])

In [33]:
# plot the box plot to know the skewed features
features=['People using safely managed drinking water services % of population 2017',
       'People using safely managed sanitation services % of population 2017',
       'Access to electricity % of population 2017',
       'Renewable energy consumption % of total final energy consumption 2015_x',
       'Expenditures for R&D % of GDP 2015',
       'Urban population living in slums % of urban population 2014',
       'Ambient PM2.5 air pollution mean annual exposure micrograms per cubic meter 2016',
       'Adjusted net savings % of GNI 2017',
       'Carbon dioxide emissions per capita metric tons 2014_x',
       'Nationally protected terrestrial and marine areas % of total territorial area 2018',
       'Intentional homicides Combined source estimates per 100,000 people 2015',
       'Internet use Individuals using the Internet % of population 2017',
       'Rural population % of total 2000', 'Rural population % of total 2018',
       'Rural population growth (annual %)  2018',
       'Land area sq. km thousands 2016',
       'Land use Forest area % of land area 2000',
       'Land use Forest area % of land area 2016',
       'Land use Permanent cropland % of land area 2000',
       'Land use Permanent cropland % of land area 2016',
       'Land use Arable land % of land area 2000',
       'Land use Arable land % of land area 2016',
       'Arable land hectares per person 2000',
       'Arable land hectares per person 2016',
       'Access to electricity % of population 2000',
       'Access to electricity % of population 2016',
       'Access to electricity % of urban population 2016',
       'Access to electricity % of rural population 2016',
       'Access to clean fuels and technologies for cooking % of population 2000',
       'Access to clean fuels and technologies for cooking % of population 2016',
       'Renewable energy consumption % of total final energy consumption 2000',
       'Renewable energy consumption % of total final energy consumption 2015_y',
       'Renewable electricity output % of total electricity output 2000',
       'Renewable electricity output % of total electricity output 2015',
       'Agricultural land % of land area 2000-02',
       'Agricultural land % of land area 2014-16',
       'Agricultural land % irrigated 2014-16',
       'Average annual precipitation millimeters 2014',
       'Land under cereal production hectares thousands 2000-02',
       'Land under cereal production hectares thousands 2014-16',
       'Fertilizer consumption % of fertilizer production 2014-16',
       'Fertilizer consumption kilograms per hectare of arable land 2014-16',
       'Agricultural employment % of total employment 2000-02',
       'Agricultural employment % of total employment 2014-16',
       'Agricultural machinery tractors per 100 sq. km of arable land 2000',
       'Agricultural machinery tractors per 100 sq. km of arable land 2009',
       'Exposure to impact Land area where elevation is below 5 meters % of land area 2010',
       'Exposure to impact Population living in areas where elevation is below 5 meters % of total population 2010',
       'Exposure to impact Population affected by droughts, floods, and extreme temperatures average annual; % of total population 2009',
       'Exposure to impact Urban land area where elevation is below 5 meters % of urban land area 2010',
       'Exposure to impact Rural population living in areas where elevation is below 5 meters % of rural population 2010',
       'Exposure to impact Rural land area where elevation is below 5 meters % of rural land area 2010',
       'Exposure to impact Urban population living in areas where elevation is below 5 meters % of urban population 2010',
       'Resilience Disaster risk reduction progress score 1, worst to 5,best 2011',
       'Net energy imports % of energy use 1990',
       'Net energy imports % of energy use 2015',
       'GDP per unit of energy use 2011 PPP $ per kilogram of oil equivalent 1990',
       'GDP per unit of energy use 2011 PPP $ per kilogram of oil equivalent 2015',
       'Carbon dioxide emissions Total thousand metric tons 1990',
       'Carbon dioxide emissions Total thousand metric tons 2014',
       'Carbon dioxide emissions Carbon intensity kilograms per kilograms of oil equivalent energy use 1990',
       'Carbon dioxide emissions Carbon intensity kilograms per kilograms of oil equivalent energy use 2014',
       'Carbon dioxide emissions per capita metric tons 1990',
       'Carbon dioxide emissions per capita metric tons 2014_y',
       'Carbon dioxide emissions kilograms per 2011 PPP $ of GDP 1990',
       'Carbon dioxide emissions kilograms per 2011 PPP $ of GDP 2014',
       'Annual freshwater withdrawals Flows billion cu. m 2014',
       'Annual freshwater withdrawals billion cu. m 2014',
       'Annual freshwater withdrawals % of internal resources 2014',
       'Annual freshwater withdrawals % for agriculture 2015',
       'Annual freshwater withdrawals % for industry 2014',
       'Water productivity % of domestic 2015',
       'People using at least basic drinking water services GDP/water use 2010 $ per cu. m 2015',
       'People using at least basic drinking water services Urban % of urban population 2018',
       'People using at least basic drinking water services Rural % of Rural population 2018',
       'Total greenhouse gas emissions thousand metric tons of carbon dioxide equivalent 2012',
       'Total greenhouse gas emissions % change 1990-2012',
       'Methane emissions thousand metric tons of carbon dioxide equivalent 2012',
       'Methane emissions % change 1990-2012',
       'Methane emissions From energy processes % of total 2008',
       'Methane emissions Agricultural % of total 2008',
       'Nitrous oxide emissions thousand metric tons of carbon dioxide equivalent 2012',
       'Nitrous oxide emissions % change 1990-2012',
       'Nitrous oxide emissions From energy processes % of total 2008',
       'Nitrous oxide emissions Agricultural % of total 2008',
       'Other greenhouse gas emissions thousand metric tons of carbon dioxide equivalent 2012',
       'Other greenhouse gas emissions % change 1990-2012',
       'Health expenditure Current % of GDP 2016',
       'Health expenditure Public % of current 2016',
       'Health expenditure Out of pocket % of current 2016',
       'Health expenditure per capita $ 2016',
       'Health expenditure per capita current PPP $ 2016',
       'External health expenditure (% of current health expenditure)  2016',
       'Health workers Physicians per 1,000 people 2009-18',
       'Health workers Nurses and midwives per 1,000 people 2009-18',
       'Specialist surgical workforce per 100,000 population 2008-18',
       'Completeness of birth registration % 2009-18',
       'Completeness of death registration % 2008-16',
       'Incidence of tuberculosis per 100,000 people 2018']
#Create a copy of the Dataframe with the selected features
df_temp = df.drop(columns=['output']).copy()

#Create, fit and transform the class OutliersRemover()
remove_outliers = OutliersRemover()
df_temp_without_outliers = remove_outliers.fit_transform(df_temp)

#Transform array back to a DataFrame
df_temp_transformed = pd.DataFrame(data = df_temp_without_outliers, columns = features)

#Plot boxplot
plot_boxplot(df_temp_transformed, features)
plt.savefig('Box Plot of feature.png')
files.download('Box Plot of feature.png')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [34]:
# defining x and y
X= df.drop(columns=['Incidence of tuberculosis per 100,000 people 2018','output'])
y = df['Incidence of tuberculosis per 100,000 people 2018']

In [35]:
# split the data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=0)

In [36]:
# scaling the data
scaler = StandardScaler()

# Fit the StandardScaler
X_scaler = scaler.fit(X_train)

# Scale the data
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

X_test_scaled.shape

(65, 98)

In [37]:
# Create a copy of the Dataframe with the selected features
df_temp = X_test_scaled.copy()
features=['People using safely managed drinking water services % of population 2017',
       'People using safely managed sanitation services % of population 2017',
       'Access to electricity % of population 2017',
       'Renewable energy consumption % of total final energy consumption 2015_x',
       'Expenditures for R&D % of GDP 2015',
       'Urban population living in slums % of urban population 2014',
       'Ambient PM2.5 air pollution mean annual exposure micrograms per cubic meter 2016',
       'Adjusted net savings % of GNI 2017',
       'Carbon dioxide emissions per capita metric tons 2014_x',
       'Nationally protected terrestrial and marine areas % of total territorial area 2018',
       'Intentional homicides Combined source estimates per 100,000 people 2015',
       'Internet use Individuals using the Internet % of population 2017',
       'Rural population % of total 2000', 'Rural population % of total 2018',
       'Rural population growth (annual %)  2018',
       'Land area sq. km thousands 2016',
       'Land use Forest area % of land area 2000',
       'Land use Forest area % of land area 2016',
       'Land use Permanent cropland % of land area 2000',
       'Land use Permanent cropland % of land area 2016',
       'Land use Arable land % of land area 2000',
       'Land use Arable land % of land area 2016',
       'Arable land hectares per person 2000',
       'Arable land hectares per person 2016',
       'Access to electricity % of population 2000',
       'Access to electricity % of population 2016',
       'Access to electricity % of urban population 2016',
       'Access to electricity % of rural population 2016',
       'Access to clean fuels and technologies for cooking % of population 2000',
       'Access to clean fuels and technologies for cooking % of population 2016',
       'Renewable energy consumption % of total final energy consumption 2000',
       'Renewable energy consumption % of total final energy consumption 2015_y',
       'Renewable electricity output % of total electricity output 2000',
       'Renewable electricity output % of total electricity output 2015',
       'Agricultural land % of land area 2000-02',
       'Agricultural land % of land area 2014-16',
       'Agricultural land % irrigated 2014-16',
       'Average annual precipitation millimeters 2014',
       'Land under cereal production hectares thousands 2000-02',
       'Land under cereal production hectares thousands 2014-16',
       'Fertilizer consumption % of fertilizer production 2014-16',
       'Fertilizer consumption kilograms per hectare of arable land 2014-16',
       'Agricultural employment % of total employment 2000-02',
       'Agricultural employment % of total employment 2014-16',
       'Agricultural machinery tractors per 100 sq. km of arable land 2000',
       'Agricultural machinery tractors per 100 sq. km of arable land 2009',
       'Exposure to impact Land area where elevation is below 5 meters % of land area 2010',
       'Exposure to impact Population living in areas where elevation is below 5 meters % of total population 2010',
       'Exposure to impact Population affected by droughts, floods, and extreme temperatures average annual; % of total population 2009',
       'Exposure to impact Urban land area where elevation is below 5 meters % of urban land area 2010',
       'Exposure to impact Rural population living in areas where elevation is below 5 meters % of rural population 2010',
       'Exposure to impact Rural land area where elevation is below 5 meters % of rural land area 2010',
       'Exposure to impact Urban population living in areas where elevation is below 5 meters % of urban population 2010',
       'Resilience Disaster risk reduction progress score 1, worst to 5,best 2011',
       'Net energy imports % of energy use 1990',
       'Net energy imports % of energy use 2015',
       'GDP per unit of energy use 2011 PPP $ per kilogram of oil equivalent 1990',
       'GDP per unit of energy use 2011 PPP $ per kilogram of oil equivalent 2015',
       'Carbon dioxide emissions Total thousand metric tons 1990',
       'Carbon dioxide emissions Total thousand metric tons 2014',
       'Carbon dioxide emissions Carbon intensity kilograms per kilograms of oil equivalent energy use 1990',
       'Carbon dioxide emissions Carbon intensity kilograms per kilograms of oil equivalent energy use 2014',
       'Carbon dioxide emissions per capita metric tons 1990',
       'Carbon dioxide emissions per capita metric tons 2014_y',
       'Carbon dioxide emissions kilograms per 2011 PPP $ of GDP 1990',
       'Carbon dioxide emissions kilograms per 2011 PPP $ of GDP 2014',
       'Annual freshwater withdrawals Flows billion cu. m 2014',
       'Annual freshwater withdrawals billion cu. m 2014',
       'Annual freshwater withdrawals % of internal resources 2014',
       'Annual freshwater withdrawals % for agriculture 2015',
       'Annual freshwater withdrawals % for industry 2014',
       'Water productivity % of domestic 2015',
       'People using at least basic drinking water services GDP/water use 2010 $ per cu. m 2015',
       'People using at least basic drinking water services Urban % of urban population 2018',
       'People using at least basic drinking water services Rural % of Rural population 2018',
       'Total greenhouse gas emissions thousand metric tons of carbon dioxide equivalent 2012',
       'Total greenhouse gas emissions % change 1990-2012',
       'Methane emissions thousand metric tons of carbon dioxide equivalent 2012',
       'Methane emissions % change 1990-2012',
       'Methane emissions From energy processes % of total 2008',
       'Methane emissions Agricultural % of total 2008',
       'Nitrous oxide emissions thousand metric tons of carbon dioxide equivalent 2012',
       'Nitrous oxide emissions % change 1990-2012',
       'Nitrous oxide emissions From energy processes % of total 2008',
       'Nitrous oxide emissions Agricultural % of total 2008',
       'Other greenhouse gas emissions thousand metric tons of carbon dioxide equivalent 2012',
       'Other greenhouse gas emissions % change 1990-2012',
       'Health expenditure Current % of GDP 2016',
       'Health expenditure Public % of current 2016',
       'Health expenditure Out of pocket % of current 2016',
       'Health expenditure per capita $ 2016',
       'Health expenditure per capita current PPP $ 2016',
       'External health expenditure (% of current health expenditure)  2016',
       'Health workers Physicians per 1,000 people 2009-18',
       'Health workers Nurses and midwives per 1,000 people 2009-18',
       'Specialist surgical workforce per 100,000 population 2008-18',
       'Completeness of birth registration % 2009-18',
       'Completeness of death registration % 2008-16']
#Create, fit and transform the class OutliersRemover()
remove_outliers = OutliersRemover()
df_temp_without_outliers = remove_outliers.fit_transform(df_temp)

#Transform array back to a DataFrame
df_temp_transformed = pd.DataFrame(data = df_temp_without_outliers, columns = features)

#Plot boxplot
plot_boxplot(df_temp_transformed, features)
plt.savefig('Box Plot of scaled feature.png')
files.download('Box Plot of scaled feature.png')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>